In [4]:
%matplotlib osx 

import numpy as np
import matplotlib.pyplot as plt
import math
from matplotlib.animation import FFMpegWriter

In [5]:
def drawAntHole(A, radius, holeC):
    N = len(A)
    midP = N//2
    A[midP-radius:midP+radius, midP-radius:midP+radius] = holeC

In [6]:
def foodBound(A, i, j):
    N = len(A)
    midP = N//2
    midP2 = midP//2
    return (i < midP2 or i > (midP+midP2)) and (j < midP2 or j > (midP+midP2))

def fillWithFood(A, foodC):
    N = len(A)
    for i in range(N):
        for j in range(N):
            foodProb = np.random.random()
            if (foodProb > 0.9 and A[i, j] == 0 and foodBound(A, i, j)):
                A[i, j] = foodC

In [16]:
def display(A, foodCounts):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]

    #Display the graphics outside of the notebook. 
    #On a PC, use '%matplotlib qt' instead.
    %matplotlib osx 
    
    f, (ax1, ax2) = plt.subplots(1, 2)
    ax1.imshow(B, cmap="BrBG"); 
    ax1.axis('off'); 
    ax1.set_title('Ant Colony Food Simulation')
    ax2.set_title('Food Count vs. Time')
    ax2.plot(list(range(len(foodCounts))), foodCounts)
    plt.pause(0.01)
    
nAnts = 50
maxX = 100
maxY = 100
midP = maxX//2
radius = 3

"""
Legend:
0 = Ground
1 = Regular Ant
2 = Food
3 = Pheromone Trail
4 = Ant with Food
5 = Ant Hole
"""

groundC = 0
foodC = 2
holeC = 5
regAntC = 1 
foodAntC = 4
pherC = 3

A = np.zeros((maxX, maxY))
drawAntHole(A, radius, holeC)
fillWithFood(A, foodC)

validStarts = []
for i in range(midP-radius-1, midP+radius+1):
    for j in range(midP-radius-1, midP+radius+1):
        if(A[i, j] == 0):
            validStarts.append((i, j))

positions = []
antType = []
onPher = []
for i in range(0,nAnts):
    randomStart = validStarts[np.random.choice(len(validStarts))]
    x  = randomStart[0]
    y  = randomStart[1]
    A[x,y] = regAntC
    positions.append((x, y))
    antType.append(regAntC)
    onPher.append(False)
    
def count(A):
    ants = 0
    food = 0
    for i in range(len(A)):
        for j in range(len(A)):
            if (A[i, j] == foodC):
                food += 1
            if (A[i, j] == regAntC or A[i, j] == foodAntC):
                ants += 1
    return ants, food

def closestFood(x, y):
    p = [x, y]
    q1 = [0, 0]
    q2 = [0, maxX]
    q3 = [maxX, 0]
    q4 = [maxX, maxX]
    dist1 = math.dist(p, q1)
    dist2 = math.dist(p, q2)
    dist3 = math.dist(p, q3)
    dist4 = math.dist(p, q4)
    
    lst = [dist1, dist2, dist3, dist4]
    lst.sort()
    if (lst[0] == dist1):
        return q1
    elif (lst[0] == dist2):
        return q2
    elif (lst[0] == dist3):
        return q3
    else:
        return q4

initialAntsCount = nAnts
initialFoodCount = count(A)[1]
time = 0

antCounts = [count(A)[0]]
foodCounts = [initialFoodCount]

while True:
    tempCount = count(A)
    antCounts.append(tempCount[0])
    foodCounts.append(tempCount[1])
    if (tempCount[1] < int(initialFoodCount*0.3)):
        break;
    time += 1
    for i in range(len(positions)):
        if (antType[i] == regAntC):
            x  = positions[i][0]
            y  = positions[i][1]
            xOrg = x
            yOrg = y
            
            if(onPher[i]):
                closest = closestFood(x, y)
                x  = positions[i][0]
                y  = positions[i][1]
                r = np.random.random()
                if (r < 0.5):
                    if (x < closest[0]):
                        x += 1
                    else:
                        x -= 1
                else:
                    if (y < closest[1]):
                        y += 1
                    else:
                        y -=1
            else:
                r = np.random.random()
                if (r < 0.25):
                    y += 1
                elif (r >= 0.25 and r < 0.5):
                    x += 1
                elif (r >= 0.5 and r < 0.75):
                    y -= 1
                else:
                    x -= 1

            if (x < 0 or y < 0 or x >= maxX or y >= maxY or A[x, y] == holeC): 
                x = xOrg
                y = yOrg
                continue;
            
            if (A[x, y] == pherC):
                onPher[i] = True

            xp = (x + 1) % maxX
            xm = (x - 1) % maxX
            yp = (y + 1) % maxY
            ym = (y - 1) % maxY

            if (antType[i] == regAntC and (A[xp, y] == foodC or A[xm, y] == foodC or A[x, yp] == foodC 
                                           or A[x, ym] == foodC)):
                A[xp, y] = groundC
                A[xm, y] = groundC
                A[x, yp] = groundC
                A[x, ym] = groundC
                antType[i] = foodAntC
                onPher[i] = False

            A[xOrg, yOrg] = groundC
            A[x,y] = antType[i]
            positions[i] = (x, y)
        else:
            x  = positions[i][0]
            y  = positions[i][1]
            r = np.random.random()
            if (r < 0.5):
                if (x < midP):
                    x += 1
                else:
                    x -= 1
            else:
                if (y < midP):
                    y += 1
                else:
                    y -=1
            
            if (x < 0 or y < 0 or x >= maxX or y >= maxY or A[x, y] == holeC): 
                x = xOrg
                y = yOrg
                continue;

            xp = (x + 1) % maxX
            xm = (x - 1) % maxX
            yp = (y + 1) % maxY
            ym = (y - 1) % maxY
            
            if (antType[i] == foodAntC and (A[xp, y] == holeC or A[xm, y] == holeC or A[x, yp] == holeC 
                                           or A[x, ym] == holeC)):
                antType[i] = regAntC
            A[xOrg, yOrg] = pherC
            A[x,y] = antType[i]
            positions[i] = (x, y)
        
    if (time % 10 == 0):
        display(A, foodCounts)

display(A, foodCounts)

In [17]:
def display(A, foodCounts):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]

    #Display the graphics outside of the notebook. 
    #On a PC, use '%matplotlib qt' instead.
    %matplotlib osx 
    
    f, (ax1, ax2) = plt.subplots(1, 2)
    ax1.imshow(B, cmap="BrBG"); 
    ax1.axis('off'); 
    ax1.set_title('Ant Colony Food Simulation')
    ax2.set_title('Food Count vs. Time')
    ax2.plot(list(range(len(foodCounts))), foodCounts)
    plt.pause(0.01)
    
nAnts = 100
maxX = 100
maxY = 100
midP = maxX//2
radius = 3

"""
Legend:
0 = Ground
1 = Regular Ant
2 = Food
3 = Pheromone Trail
4 = Ant with Food
5 = Ant Hole
"""

groundC = 0
foodC = 2
holeC = 5
regAntC = 1 
foodAntC = 4
pherC = 3

A = np.zeros((maxX, maxY))
drawAntHole(A, radius, holeC)
fillWithFood(A, foodC)

validStarts = []
for i in range(midP-radius-1, midP+radius+1):
    for j in range(midP-radius-1, midP+radius+1):
        if(A[i, j] == 0):
            validStarts.append((i, j))

positions = []
antType = []
onPher = []
for i in range(0,nAnts):
    randomStart = validStarts[np.random.choice(len(validStarts))]
    x  = randomStart[0]
    y  = randomStart[1]
    A[x,y] = regAntC
    positions.append((x, y))
    antType.append(regAntC)
    onPher.append(False)
    
def count(A):
    ants = 0
    food = 0
    for i in range(len(A)):
        for j in range(len(A)):
            if (A[i, j] == foodC):
                food += 1
            if (A[i, j] == regAntC or A[i, j] == foodAntC):
                ants += 1
    return ants, food

def closestFood(x, y):
    p = [x, y]
    q1 = [0, 0]
    q2 = [0, maxX]
    q3 = [maxX, 0]
    q4 = [maxX, maxX]
    dist1 = math.dist(p, q1)
    dist2 = math.dist(p, q2)
    dist3 = math.dist(p, q3)
    dist4 = math.dist(p, q4)
    
    lst = [dist1, dist2, dist3, dist4]
    lst.sort()
    if (lst[0] == dist1):
        return q1
    elif (lst[0] == dist2):
        return q2
    elif (lst[0] == dist3):
        return q3
    else:
        return q4

initialAntsCount = nAnts
initialFoodCount = count(A)[1]
time = 0

antCounts = [count(A)[0]]
foodCounts = [initialFoodCount]

while True:
    tempCount = count(A)
    antCounts.append(tempCount[0])
    foodCounts.append(tempCount[1])
    if (tempCount[1] < int(initialFoodCount*0.3)):
        break;
    time += 1
    for i in range(len(positions)):
        if (antType[i] == regAntC):
            x  = positions[i][0]
            y  = positions[i][1]
            xOrg = x
            yOrg = y
            
            if(onPher[i]):
                closest = closestFood(x, y)
                x  = positions[i][0]
                y  = positions[i][1]
                r = np.random.random()
                if (r < 0.5):
                    if (x < closest[0]):
                        x += 1
                    else:
                        x -= 1
                else:
                    if (y < closest[1]):
                        y += 1
                    else:
                        y -=1
            else:
                r = np.random.random()
                if (r < 0.25):
                    y += 1
                elif (r >= 0.25 and r < 0.5):
                    x += 1
                elif (r >= 0.5 and r < 0.75):
                    y -= 1
                else:
                    x -= 1

            if (x < 0 or y < 0 or x >= maxX or y >= maxY or A[x, y] == holeC): 
                x = xOrg
                y = yOrg
                continue;
            
            if (A[x, y] == pherC):
                onPher[i] = True

            xp = (x + 1) % maxX
            xm = (x - 1) % maxX
            yp = (y + 1) % maxY
            ym = (y - 1) % maxY

            if (antType[i] == regAntC and (A[xp, y] == foodC or A[xm, y] == foodC or A[x, yp] == foodC 
                                           or A[x, ym] == foodC)):
                A[xp, y] = groundC
                A[xm, y] = groundC
                A[x, yp] = groundC
                A[x, ym] = groundC
                antType[i] = foodAntC
                onPher[i] = False

            A[xOrg, yOrg] = groundC
            A[x,y] = antType[i]
            positions[i] = (x, y)
        else:
            x  = positions[i][0]
            y  = positions[i][1]
            r = np.random.random()
            if (r < 0.5):
                if (x < midP):
                    x += 1
                else:
                    x -= 1
            else:
                if (y < midP):
                    y += 1
                else:
                    y -=1
            
            if (x < 0 or y < 0 or x >= maxX or y >= maxY or A[x, y] == holeC): 
                x = xOrg
                y = yOrg
                continue;

            xp = (x + 1) % maxX
            xm = (x - 1) % maxX
            yp = (y + 1) % maxY
            ym = (y - 1) % maxY
            
            if (antType[i] == foodAntC and (A[xp, y] == holeC or A[xm, y] == holeC or A[x, yp] == holeC 
                                           or A[x, ym] == holeC)):
                antType[i] = regAntC
            A[xOrg, yOrg] = pherC
            A[x,y] = antType[i]
            positions[i] = (x, y)
        
    if (time % 10 == 0):
        display(A, foodCounts)

display(A, foodCounts)